In [1]:
gameFolder = "DOA++-MAME"
#gameFolder = "SFIII-MAME"
#gameFolder = "UMK3-MAME"
#gameFolder = "TEKTAG-MAME"

In [2]:
import sys, os
import time
timeDepSeed = int((time.time()-int(time.time()-0.5))*1000)

sys.path.append(os.path.join(os.path.abspath(''), '../../games',gameFolder))   

tensorBoardFolder = "./ppo2_TB_CustCnnLnLstm_" + gameFolder + "/"
modelFolder = "ppo2_Model_CustCnnLnLstm_" + gameFolder

In [3]:
from makeDiambraEnv import *

import tensorflow as tf

%load_ext tensorboard

from stable_baselines.common.policies import RecurrentActorCriticPolicy
from stable_baselines.common.policies import *
from stable_baselines import PPO2
from stable_baselines.common.evaluation import evaluate_policy

In [4]:
class CustomCnnLstmPolicy(RecurrentActorCriticPolicy):
    """
    Policy object that implements actor critic, using LSTMs.

    :param sess: (TensorFlow session) The current TensorFlow session
    :param ob_space: (Gym Space) The observation space of the environment
    :param ac_space: (Gym Space) The action space of the environment
    :param n_env: (int) The number of environments to run
    :param n_steps: (int) The number of steps to run for each environment
    :param n_batch: (int) The number of batch to run (n_envs * n_steps)
    :param n_lstm: (int) The number of LSTM cells (for recurrent policies)
    :param reuse: (bool) If the policy is reusable or not
    :param layers: ([int]) The size of the Neural network before the LSTM layer  (if None, default to [64, 64])
    :param net_arch: (list) Specification of the actor-critic policy network architecture. Notation similar to the
        format described in mlp_extractor but with additional support for a 'lstm' entry in the shared network part.
    :param act_fun: (tf.func) the activation function to use in the neural network.
    :param cnn_extractor: (function (TensorFlow Tensor, ``**kwargs``): (TensorFlow Tensor)) the CNN feature extraction
    :param layer_norm: (bool) Whether or not to use layer normalizing LSTMs
    :param feature_extraction: (str) The feature extraction type ("cnn" or "mlp")
    :param kwargs: (dict) Extra keyword arguments for the nature CNN feature extraction
    """

    recurrent = True

    def __init__(self, sess, ob_space, ac_space, n_env, n_steps, n_batch, n_lstm=256, reuse=False, 
                 layers=None, net_arch=None, act_fun=tf.tanh, cnn_extractor=nature_cnn, 
                 layer_norm=True, feature_extraction="cnn", **kwargs):
        
        # state_shape = [n_lstm * 2] dim because of the cell and hidden states of the LSTM
        super(CustomCnnLstmPolicy, self).__init__(sess, ob_space, ac_space, n_env, n_steps, n_batch,
                                         state_shape=(2 * n_lstm, ), reuse=reuse,
                                         scale=(feature_extraction == "cnn"))

      
        self._kwargs_check(feature_extraction, kwargs)
       
        frames = self.processed_obs[:,:,:,0:4]
        additional_input = self.processed_obs[:,:,:,4]
        additional_input = tf.layers.flatten(additional_input)
        additional_input = additional_input[:,1:149]
        
        if layers is None:
            layers = [64, 64]
        else:
            warnings.warn("The layers parameter is deprecated. Use the net_arch parameter instead.")

        with tf.variable_scope("model", reuse=reuse):
            
            # Frames (CNN)
            extracted_features_frames = cnn_extractor(frames, **kwargs)
            
            # Additional (Additional Info)
            for i, layer_size in enumerate(layers):
                extracted_features_addinfo = act_fun(linear(additional_input, 'pi_fc' + str(i), 
                                                            n_hidden=layer_size, init_scale=np.sqrt(2)))
            
            extracted_features = tf.concat([extracted_features_frames, extracted_features_addinfo], 1)
            
            #print("Extracted feat frames")
            #print(extracted_features_frames)
            #print("Extracted feat additional info")
            #print(extracted_features_addinfo)
            #print("Extracted feat")
            #print(extracted_features)
            input_sequence = batch_to_seq(extracted_features, self.n_env, n_steps)
            #print("input_sequence")
            #print(input_sequence)
            #print("dones_ph")
            #print(self.dones_ph)
            masks = batch_to_seq(self.dones_ph, self.n_env, n_steps)
            #print("masks")
            #print(masks)
            rnn_output, self.snew = lstm(input_sequence, masks, self.states_ph, 'lstm1', n_hidden=n_lstm,
                                         layer_norm=layer_norm)
            #print("rnn_output")
            #print(rnn_output)
            #input("Pause")
            rnn_output = seq_to_batch(rnn_output)
            value_fn = linear(rnn_output, 'vf', 1)

            self._proba_distribution, self._policy, self.q_value = \
                self.pdtype.proba_distribution_from_latent(rnn_output, rnn_output)

        self._value_fn = value_fn
        
        self._setup_init()

    def step(self, obs, state=None, mask=None, deterministic=False):
        if deterministic:
            return self.sess.run([self.deterministic_action, self.value_flat, self.snew, self.neglogp],
                                 {self.obs_ph: obs, self.states_ph: state, self.dones_ph: mask})
        else:
            return self.sess.run([self.action, self.value_flat, self.snew, self.neglogp],
                                 {self.obs_ph: obs, self.states_ph: state, self.dones_ph: mask})

    def proba_step(self, obs, state=None, mask=None):
        return self.sess.run(self.policy_proba, {self.obs_ph: obs, self.states_ph: state, self.dones_ph: mask})

    def value(self, obs, state=None, mask=None):
        return self.sess.run(self.value_flat, {self.obs_ph: obs, self.states_ph: state, self.dones_ph: mask})


In [9]:
diambraKwargs = {}
diambraKwargs["roms_path"] = "../../roms/MAMEToolkit/roms/"
diambraKwargs["binary_path"] = "../../../customMAME/"
diambraKwargs["player"] = "P1"
diambraKwargs["frame_ratio"] = 3
#diambraKwargs["render"] =True
#diambraKwargs["throttle"] = False
#diambraKwargs["sound"] = False 
#diambraKwargs["character"] ="Random"
diambraKwargs["character"] = "Kasumi"

wrapperKwargs = {}
wrapperKwargs["frame_stack"] = 4
wrapperKwargs["clip_rewards"] = False
wrapperKwargs["normalize_rewards"] = True
wrapperKwargs["scale"] = True
wrapperKwargs["hw_obs_resize"] = [256, 256]

#keyToAdd = None
keyToAdd = []
keyToAdd.append("actionsBuf")
#keyToAdd.append("player")
keyToAdd.append("healthP1")
keyToAdd.append("healthP2")
keyToAdd.append("positionP1")
keyToAdd.append("positionP2")
#keyToAdd.append("winsP1")
#keyToAdd.append("winsP2")

numEnv=1

env = make_diambra_env(diambraMame, env_prefix="Train", num_env=numEnv, seed=timeDepSeed, continue_game = False,
                       diambra_kwargs = diambraKwargs, wrapper_kwargs = wrapperKwargs, 
                       key_to_add = keyToAdd)

# OR 
#env = make_diambra_env(diambraMame, num_env=2, seed=0, diambra_kwargs = diambraKwargs)
# Frame-stacking with 4 frames
#env = VecFrameStack(env, n_stack=4)

Env_id =  Train0
Continue rule =  False
Player = P1 , Character = Kasumi
Noop action N =  11


In [ ]:
print("Obs_space = ", env.observation_space)
print("Obs_space type = ", env.observation_space.dtype)
print("Obs_space high = ", env.observation_space.high)
print("Obs_space low = ", env.observation_space.low)

In [ ]:
print("Act_space = ", env.action_space)
print("Act_space type = ", env.action_space.dtype)
print("Act_space n = ", env.action_space.n)

In [10]:
policyKwargs={}
policyKwargs["layers"] = [128, 256]

# Initialize the model, 1 env
#model = PPO2(CustomCnnLstmPolicy, env, nminibatches=1, verbose=1, 
#             tensorboard_log=tensorBoardFolder, policy_kwargs=policyKwargs, gamma = 0.9)

#OR

# Load the trained agent, 1 env
model = PPO2.load(modelFolder+"2Msteps_action+_add", env=env, tensorboard_log=tensorBoardFolder, 
                  policy_kwargs=policyKwargs, gamma = 0.9)

Instructions for updating:
Use keras.layers.flatten instead.


Instructions for updating:
Use keras.layers.flatten instead.


/home/alexpalms/anaconda3/envs/diambra/lib/python3.6/site-packages/ipykernel_launcher.py:45: UserWarning: The layers parameter is deprecated. Use the net_arch parameter instead.


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [ ]:
# Train the agent
time_steps = 10000000
model.learn(total_timesteps=time_steps)

Setting difficulty = 3
Starting game
Selecting Kasumi
Waiting for fight to start
--------------------------------------
| approxkl           | 4.0789753e-05 |
| clipfrac           | 0.0           |
| explained_variance | -0.0119       |
| fps                | 2             |
| n_updates          | 1             |
| policy_entropy     | 1.6001147     |
| policy_loss        | -0.0013653897 |
| serial_timesteps   | 128           |
| time_elapsed       | 1.88e-05      |
| total_timesteps    | 128           |
| value_loss         | 0.003962788   |
--------------------------------------
---------------------------------------
| approxkl           | 1.25722145e-05 |
| clipfrac           | 0.0            |
| explained_variance | 0.0217         |
| fps                | 24             |
| n_updates          | 2              |
| policy_entropy     | 1.9708548      |
| policy_loss        | -0.0006090328  |
| serial_timesteps   | 256            |
| time_elapsed       | 44.3           |
| total_time

--------------------------------------
| approxkl           | 1.4027405e-06 |
| clipfrac           | 0.0           |
| explained_variance | 0.00131       |
| fps                | 24            |
| n_updates          | 17            |
| policy_entropy     | 2.1540644     |
| policy_loss        | -0.0002354905 |
| serial_timesteps   | 2176          |
| time_elapsed       | 164           |
| total_timesteps    | 2176          |
| value_loss         | 0.002680947   |
--------------------------------------
Round done
--------------------------------------
| approxkl           | 8.313155e-07  |
| clipfrac           | 0.0           |
| explained_variance | -0.000547     |
| fps                | 12            |
| n_updates          | 18            |
| policy_entropy     | 2.1564045     |
| policy_loss        | -9.794533e-05 |
| serial_timesteps   | 2304          |
| time_elapsed       | 169           |
| total_timesteps    | 2304          |
| value_loss         | 0.010908103   |
--------------

Round done
---------------------------------------
| approxkl           | 1.3765451e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.99e+03       |
| ep_reward_mean     | 6.72           |
| explained_variance | -0.0766        |
| fps                | 11             |
| n_updates          | 33             |
| policy_entropy     | 1.9954724      |
| policy_loss        | -1.5996397e-05 |
| serial_timesteps   | 4224           |
| time_elapsed       | 291            |
| total_timesteps    | 4224           |
| value_loss         | 0.003941361    |
---------------------------------------
---------------------------------------
| approxkl           | 8.440321e-07   |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.99e+03       |
| ep_reward_mean     | 6.72           |
| explained_variance | -0.00188       |
| fps                | 24             |
| n_updates          | 34             |
| policy_entropy     | 2.060729       |
| policy_loss        | -0.000

--------------------------------------
| approxkl           | 1.0455842e-05 |
| clipfrac           | 0.0           |
| ep_len_mean        | 2.92e+03      |
| ep_reward_mean     | 5.35          |
| explained_variance | 0.0858        |
| fps                | 24            |
| n_updates          | 47            |
| policy_entropy     | 1.9043531     |
| policy_loss        | -8.40947e-05  |
| serial_timesteps   | 6016          |
| time_elapsed       | 409           |
| total_timesteps    | 6016          |
| value_loss         | 0.0065526366  |
--------------------------------------
---------------------------------------
| approxkl           | 2.6895104e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 2.92e+03       |
| ep_reward_mean     | 5.35           |
| explained_variance | 0.0165         |
| fps                | 24             |
| n_updates          | 48             |
| policy_entropy     | 2.0478058      |
| policy_loss        | -0.00016534887 |
| serial_timest

Round done
---------------------------------------
| approxkl           | 6.715801e-07   |
| clipfrac           | 0.0            |
| ep_len_mean        | 2.92e+03       |
| ep_reward_mean     | 5.35           |
| explained_variance | 0.000551       |
| fps                | 11             |
| n_updates          | 61             |
| policy_entropy     | 2.1927037      |
| policy_loss        | -0.00019744411 |
| serial_timesteps   | 7808           |
| time_elapsed       | 511            |
| total_timesteps    | 7808           |
| value_loss         | 0.006978983    |
---------------------------------------
--------------------------------------
| approxkl           | 1.5578835e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 2.92e+03      |
| ep_reward_mean     | 5.35          |
| explained_variance | 0.00182       |
| fps                | 24            |
| n_updates          | 62            |
| policy_entropy     | 2.1966536     |
| policy_loss        | -0.0001629442 |

...

--------------------------------------
| approxkl           | 2.6120185e-07 |
| clipfrac           | 0.0           |
| ep_len_mean        | 3.25e+03      |
| ep_reward_mean     | 4.13          |
| explained_variance | -0.000334     |
| fps                | 23            |
| n_updates          | 6573          |
| policy_entropy     | 2.368257      |
| policy_loss        | 4.503876e-06  |
| serial_timesteps   | 841344        |
| time_elapsed       | 5.26e+04      |
| total_timesteps    | 841344        |
| value_loss         | 0.0054842616  |
--------------------------------------
Episode done
Restarting game
Selecting Kasumi
Waiting for fight to start
-------------------------------------
| approxkl           | 6.375276e-07 |
| clipfrac           | 0.0          |
| ep_len_mean        | 3.23e+03     |
| ep_reward_mean     | 4.04         |
| explained_variance | 0.0431       |
| fps                | 8            |
| n_updates          | 6574         |
| policy_entropy     | 2.354268     |


--------------------------------------
| approxkl           | 1.4773326e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 3.23e+03      |
| ep_reward_mean     | 4.04          |
| explained_variance | -0.00021      |
| fps                | 23            |
| n_updates          | 6587          |
| policy_entropy     | 2.354459      |
| policy_loss        | -0.0002020523 |
| serial_timesteps   | 843136        |
| time_elapsed       | 5.27e+04      |
| total_timesteps    | 843136        |
| value_loss         | 0.010309586   |
--------------------------------------
Round done
---------------------------------------
| approxkl           | 1.8341467e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.23e+03       |
| ep_reward_mean     | 4.04           |
| explained_variance | -0.00205       |
| fps                | 10             |
| n_updates          | 6588           |
| policy_entropy     | 2.3529413      |
| policy_loss        | -0.00010332465 |
| se

---------------------------------------
| approxkl           | 2.5990892e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.21e+03       |
| ep_reward_mean     | 4.01           |
| explained_variance | 0.00441        |
| fps                | 22             |
| n_updates          | 6601           |
| policy_entropy     | 2.3375492      |
| policy_loss        | -0.00018807873 |
| serial_timesteps   | 844928         |
| time_elapsed       | 5.28e+04       |
| total_timesteps    | 844928         |
| value_loss         | 0.0034098884   |
---------------------------------------
---------------------------------------
| approxkl           | 1.9255353e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.21e+03       |
| ep_reward_mean     | 4.01           |
| explained_variance | 0.006          |
| fps                | 22             |
| n_updates          | 6602           |
| policy_entropy     | 2.337173       |
| policy_loss        | -0.00014581252 |


--------------------------------------
| approxkl           | 2.4784292e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 3.2e+03       |
| ep_reward_mean     | 4             |
| explained_variance | 0.0113        |
| fps                | 22            |
| n_updates          | 6615          |
| policy_entropy     | 2.3316655     |
| policy_loss        | -0.0003100671 |
| serial_timesteps   | 846720        |
| time_elapsed       | 5.29e+04      |
| total_timesteps    | 846720        |
| value_loss         | 0.0033284973  |
--------------------------------------
Stage done
--------------------------------------
| approxkl           | 1.913679e-06  |
| clipfrac           | 0.0           |
| ep_len_mean        | 3.2e+03       |
| ep_reward_mean     | 4             |
| explained_variance | 0.00287       |
| fps                | 10            |
| n_updates          | 6616          |
| policy_entropy     | 2.3367488     |
| policy_loss        | 5.2690506e-05 |
| serial_times

Round done
--------------------------------------
| approxkl           | 1.7725932e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 3.2e+03       |
| ep_reward_mean     | 4             |
| explained_variance | -0.000407     |
| fps                | 10            |
| n_updates          | 6629          |
| policy_entropy     | 2.3379636     |
| policy_loss        | -7.83205e-05  |
| serial_timesteps   | 848512        |
| time_elapsed       | 5.3e+04       |
| total_timesteps    | 848512        |
| value_loss         | 0.005392245   |
--------------------------------------
---------------------------------------
| approxkl           | 1.297106e-06   |
| clipfrac           | 0.0            |
| ep_len_mean        | 3.2e+03        |
| ep_reward_mean     | 4              |
| explained_variance | 0.000233       |
| fps                | 22             |
| n_updates          | 6630           |
| policy_entropy     | 2.3374538      |
| policy_loss        | -0.00016903505 |
| se

In [ ]:
# Save the agent
model.save(modelFolder+"2Msteps_action+_add")

In [ ]:
%tensorboard --logdir ./tensorBoardFolder/

In [ ]:
observation = env.reset()
states = None

while True:

    action, states = model.predict(observation, states, deterministic=False)
    action_prob = model.action_probability(observation, states)
    print("Action probabilities = ", action_prob)
    print("Max action = ", np.argmax(action_prob))
    print("Action = ", action)
    input("Pausa")
    
    observation, reward, done, info = env.step(action)
    if done:
        observation = env.reset()
        states = None
        
env.close()

In [ ]:
observation = env.reset()
states = None

cumulativeEpRew = 0.0
cumulativeEpRewAll = []
cumulativeTotRew = 0.0

maxNumEp = 100
currNumEp = 0

while currNumEp < maxNumEp:

    action, states = model.predict(observation, states, deterministic=False)
    action_prob = model.action_probability(observation, states)
    print("Action probabilities = ", action_prob)
    print("Max action = ", np.argmax(action_prob))
    print("Action = ", action)
    
    observation, reward, done, info = env.step(action)
    
    cumulativeEpRew += reward
    
    if np.any(done):
        currNumEp += 1
        print("Ep. # = ", currNumEp)
        print("Ep. Cumulative Rew # = ", cumulativeEpRew)
        sys.stdout.flush()
        cumulativeEpRewAll.append(cumulativeEpRew)
        cumulativeTotRew += cumulativeEpRew
        cumulativeEpRew = 0.0

        observation = env.reset()
        states = None

print("Mean cumulative reward = ", cumulativeTotRew/maxNumEp)    
print("Mean cumulative reward = ", np.mean(cumulativeEpRewAll))    
print("Std cumulative reward = ", np.std(cumulativeEpRewAll))   
    
env.close()